In [1]:
!pip install --upgrade paho-mqtt

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.2/67.2 KB 776.7 kB/s eta 0:00:00a 0:00:01


In [2]:
!pip install pytz

Defaulting to user installation because normal site-packages is not writeable


#All vehicles arriving

In [9]:
import paho.mqtt.client as mqtt
import json
from kafka import KafkaProducer

producer = KafkaProducer(
    bootstrap_servers=['localhost:9092'],
    value_serializer=lambda v: json.dumps(v).encode('utf-8')
)

def on_connect(client, userdata, flags, rc):
    print("Connected with result code " + str(rc))
    client.subscribe("/hfp/v2/journey/ongoing/vp/#")

def on_message(client, userdata, msg):
    try:
        message_data = json.loads(msg.payload.decode('utf-8'))
        topic_parts = msg.topic.split('/')
        combined_data = {
            "vehicle_type": topic_parts[6],
            "nextStop": topic_parts[13],
        }
        combined_data.update(message_data)
        print(json.dumps(combined_data, indent=4))
        producer.send('vp', value=combined_data)
    except json.JSONDecodeError:
        print(f"Erreur de décodage : {msg.payload.decode('utf-8')}")
    except TypeError as e:
        print(f"Erreur : {e}, Message : {msg.payload.decode('utf-8')}")

client = mqtt.Client()
client.on_connect = on_connect
client.on_message = on_message
client.tls_set()
client.connect("mqtt.hsl.fi", 8883, 60)
client.loop_start()
import time
time.sleep(5)
client.loop_stop()



/tmp/ipykernel_6526/815101945.py:30: DeprecationWarning: Callback API version 1 is deprecated, update to latest version
  client = mqtt.Client()


Connected with result code 0
{
    "vehicle_type": "tram",
    "nextStop": "1282402",
    "VP": {
        "desi": "15",
        "dir": "2",
        "oper": 40,
        "veh": 627,
        "tst": "2025-01-31T11:12:34.400Z",
        "tsi": 1738321954,
        "spd": 1.25,
        "hdg": 119,
        "lat": 60.231364,
        "long": 24.934148,
        "acc": 0.5,
        "dl": -120,
        "odo": 15046,
        "drst": 0,
        "oday": "2025-01-31",
        "jrn": 1234,
        "line": 1142,
        "start": "12:33",
        "loc": "GPS",
        "stop": 1282402,
        "route": "2015",
        "occu": 0
    }
}
{
    "vehicle_type": "tram",
    "nextStop": "1030429",
    "VP": {
        "desi": "10",
        "dir": "2",
        "oper": 40,
        "veh": 90,
        "tst": "2025-01-31T11:12:34.436Z",
        "tsi": 1738321954,
        "spd": 6.07,
        "hdg": 180,
        "lat": 60.166009,
        "long": 24.943734,
        "acc": -0.42,
        "dl": -402,
        "odo": 4795,
 

<MQTTErrorCode.MQTT_ERR_SUCCESS: 0>

In [ ]:


import requests
import json
from google.transit import gtfs_realtime_pb2
from datetime import datetime
from kafka import KafkaProducer

TRIP_UPDATES_URL = "https://realtime.hsl.fi/realtime/trip-updates/v2/hsl"
KAFKA_BROKER = 'localhost:9092'
KAFKA_TOPIC = 'trip'
MAX_MESSAGE_SIZE = 5 * 1024 * 1024  # 5 Mo

def kafka_callback(err, msg):
    if err:
        print(f"Erreur Kafka: {err}")
    else:
        print(f"Message Kafka envoyé à {msg.topic()} avec le offset {msg.offset()}")

def fetch_trip_updates_as_json():
    feed = gtfs_realtime_pb2.FeedMessage()
    trip_updates_list = []  
    
    try:
        print("Récupération des données depuis l'API...")
        response = requests.get(TRIP_UPDATES_URL, timeout=10)
        response.raise_for_status()
        
        print("Parsing des données...")
        feed.ParseFromString(response.content)
        
        for entity in feed.entity:
            if entity.HasField('trip_update'):
                trip_update = entity.trip_update
                
                # Conversion du start_date au format yyyy-MM-dd
                start_date_parsed = datetime.strptime(trip_update.trip.start_date, "%Y%m%d")
                formatted_start_date = start_date_parsed.strftime("%Y-%m-%d")
                
                trip_id_combination = f"{trip_update.trip.route_id}_{formatted_start_date}_{trip_update.trip.start_time}_{trip_update.trip.direction_id}"
                
                trip_data = {
                    "trip_id": trip_id_combination,
                    "route_id": trip_update.trip.route_id,
                    "start_date": formatted_start_date,  # Remplace start_date par le format modifié
                    "start_time": trip_update.trip.start_time,
                    "direction_id": trip_update.trip.direction_id,
                    "stop_time_updates": []
                }
                
                for stop_time_update in trip_update.stop_time_update:
                    stop_data = {
                        "stop_id": stop_time_update.stop_id,
                        "arrival_time": datetime.fromtimestamp(stop_time_update.arrival.time).isoformat() 
                                        if stop_time_update.HasField('arrival') else None,
                        "departure_time": datetime.fromtimestamp(stop_time_update.departure.time).isoformat() 
                                          if stop_time_update.HasField('departure') else None
                    }
                    trip_data["stop_time_updates"].append(stop_data)
                
                trip_updates_list.append(trip_data)
        
        serialized_data = json.dumps(trip_updates_list).encode('utf-8')
        data_size = len(serialized_data)
        
        print(f"Données récupérées ({data_size} octets) :")
        print(json.dumps(trip_updates_list, indent=4))
        
        if data_size > MAX_MESSAGE_SIZE:
            raise ValueError(f"Les données ({data_size} octets) dépassent la taille maximale autorisée ({MAX_MESSAGE_SIZE} octets).")

        print("Connexion au broker Kafka...")
        producer = KafkaProducer(
            bootstrap_servers=[KAFKA_BROKER],
            value_serializer=lambda v: json.dumps(v).encode('utf-8'),
            request_timeout_ms=5000,
            max_request_size=MAX_MESSAGE_SIZE
        )
        print("Connexion au broker Kafka réussie.")
        
        print("Envoi des données au topic Kafka...")

        # Envoi des messages un par un
        for trip_data in trip_updates_list:
            future = producer.send(KAFKA_TOPIC, value=trip_data)
            future.add_callback(kafka_callback).add_errback(kafka_callback)
            producer.flush()

        print("Données envoyées au topic Kafka.")
        
    except requests.exceptions.RequestException as e:
        print(f"Erreur lors de la récupération des données depuis l'API : {e}")
    except Exception as e:
        print(f"Erreur générale : {e}")

# Exécution de la fonction
fetch_trip_updates_as_json()


In [2]:
import requests
import json
from google.transit import gtfs_realtime_pb2
from datetime import datetime
from kafka import KafkaProducer

TRIP_UPDATES_URL = "https://realtime.hsl.fi/realtime/trip-updates/v2/hsl"
KAFKA_BROKER = 'localhost:9092'
KAFKA_TOPIC = 'trip'
MAX_MESSAGE_SIZE = 5 * 1024 * 1024  # 5 Mo

def kafka_callback(err, msg):
    if err:
        print(f"Erreur Kafka: {err}")
    else:
        print(f"Message Kafka envoyé à {msg.topic()} avec le offset {msg.offset()}")

def fetch_trip_updates_as_json():
    feed = gtfs_realtime_pb2.FeedMessage()
    trip_updates_list = []  
    
    try:
        print("Récupération des données depuis l'API...")
        response = requests.get(TRIP_UPDATES_URL, timeout=10)
        response.raise_for_status()
        
        print("Parsing des données...")
        feed.ParseFromString(response.content)
        
        for entity in feed.entity:
            if entity.HasField('trip_update'):
                trip_update = entity.trip_update
                
                # Conversion du start_date au format yyyy-MM-dd
                start_date_parsed = datetime.strptime(trip_update.trip.start_date, "%Y%m%d")
                formatted_start_date = start_date_parsed.strftime("%Y-%m-%d")
                
                trip_id_combination = f"{trip_update.trip.route_id}_{formatted_start_date}_{trip_update.trip.start_time}_{trip_update.trip.direction_id}"
                
                trip_data = {
                    "trip_id": trip_id_combination,
                    "route_id": trip_update.trip.route_id,
                    "start_date": formatted_start_date,  # Remplace start_date par le format modifié
                    "start_time": trip_update.trip.start_time,
                    "direction_id": trip_update.trip.direction_id,
                    "stop_time_updates": []
                }
                
                for stop_time_update in trip_update.stop_time_update:
                    stop_data = {
                        "stop_id": stop_time_update.stop_id,
                        "arrival_time": datetime.fromtimestamp(stop_time_update.arrival.time).isoformat() 
                                        if stop_time_update.HasField('arrival') else None,
                        "departure_time": datetime.fromtimestamp(stop_time_update.departure.time).isoformat() 
                                          if stop_time_update.HasField('departure') else None
                    }
                    trip_data["stop_time_updates"].append(stop_data)
                
                trip_updates_list.append(trip_data)
        
        serialized_data = json.dumps(trip_updates_list).encode('utf-8')
        data_size = len(serialized_data)
        
        print(f"Données récupérées ({data_size} octets) :")
        print(json.dumps(trip_updates_list, indent=4))
        
        if data_size > MAX_MESSAGE_SIZE:
            raise ValueError(f"Les données ({data_size} octets) dépassent la taille maximale autorisée ({MAX_MESSAGE_SIZE} octets).")

        print("Connexion au broker Kafka...")
        producer = KafkaProducer(
            bootstrap_servers=[KAFKA_BROKER],
            value_serializer=lambda v: json.dumps(v).encode('utf-8'),
            request_timeout_ms=5000,
            max_request_size=MAX_MESSAGE_SIZE
        )
        print("Connexion au broker Kafka réussie.")
        
        print("Envoi des données au topic Kafka...")

        # Envoi des messages un par un
        for trip_data in trip_updates_list:
            future = producer.send(KAFKA_TOPIC, value=trip_data)
            future.add_callback(kafka_callback).add_errback(kafka_callback)
            producer.flush()

        print("Données envoyées au topic Kafka.")
        
    except requests.exceptions.RequestException as e:
        print(f"Erreur lors de la récupération des données depuis l'API : {e}")
    except Exception as e:
        print(f"Erreur générale : {e}")

# Exécution de la fonction
fetch_trip_updates_as_json()


Récupération des données depuis l'API...
Parsing des données...
Données récupérées (1857390 octets) :
[
    {
        "trip_id": "2105_2025-01-20_22:18:00_1",
        "route_id": "2105",
        "start_date": "2025-01-20",
        "start_time": "22:18:00",
        "direction_id": 1,
        "stop_time_updates": [
            {
                "stop_id": "2241234",
                "arrival_time": "2025-01-20T21:14:56",
                "departure_time": "2025-01-20T21:18:21"
            },
            {
                "stop_id": "2241220",
                "arrival_time": "2025-01-20T21:19:33",
                "departure_time": "2025-01-20T21:19:33"
            },
            {
                "stop_id": "2241218",
                "arrival_time": "2025-01-20T21:20:06",
                "departure_time": "2025-01-20T21:20:06"
            },
            {
                "stop_id": "2241216",
                "arrival_time": "2025-01-20T21:20:44",
                "departure_time": "2025-01-2

KeyboardInterrupt: 

In [14]:
pip install --upgrade kafka-python

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [18]:
from kafka import KafkaProducer
import json

producer = KafkaProducer(
    bootstrap_servers='localhost:9092',
    value_serializer=lambda v: json.dumps(v).encode('utf-8')
)

test_message = {"key": "value"}
try:
    producer.send('testtest', value=test_message).get(timeout=10)
    print("Message envoyé avec succès.")
except Exception as e:
    print(f"Erreur lors de l'envoi : {e}")

Message envoyé avec succès.
